# Eat Safe, Love

## Part 1: Database and Jupyter Notebook Set Up

Import the data provided in the `establishments.json` file from your Terminal. Name the database `uk_food` and the collection `establishments`.

Within this markdown cell, copy the line of text you used to import the data from your Terminal. This way, future analysts will be able to repeat your process.

e.g.: Import the dataset with ` mongoimport --type json -d uk_food -c establishments --drop --jsonArray establishments.json`

In [1]:
# Import dependencies
from pymongo import MongoClient
from pprint import pprint

In [2]:
# Create an instance of MongoClient
mongo = MongoClient(port=27017)

In [3]:
# confirm that our new database was created
print(mongo.list_database_names())

['admin', 'autosaurus', 'config', 'fruits_db', 'local', 'met', 'uk_food']


In [4]:
# assign the uk_food database to a variable name
db = mongo['uk_food']

In [10]:
# review the collections in our new database
print(db.list_collection_names())

['establishments']


In [8]:
# review the collections in our new database
print(db.list_collection_names())

['establishments']


In [9]:
# review a document in the establishments collection
pprint(db.establishments.find_one())

{'AddressLine1': 'The Bay',
 'AddressLine2': 'St Margarets Bay',
 'AddressLine3': 'Kent',
 'AddressLine4': '',
 'BusinessName': 'The Coastguard Inn',
 'BusinessType': 'Pub/bar/nightclub',
 'BusinessTypeID': 7843,
 'ChangesByServerID': 0,
 'Distance': 4587.347174863443,
 'FHRSID': 1034540,
 'LocalAuthorityBusinessID': 'PI/000078691',
 'LocalAuthorityCode': '182',
 'LocalAuthorityEmailAddress': 'publicprotection@dover.gov.uk',
 'LocalAuthorityName': 'Dover',
 'LocalAuthorityWebSite': 'http://www.dover.gov.uk/',
 'NewRatingPending': False,
 'Phone': '',
 'PostCode': 'CT15 6DY',
 'RatingDate': '2022-08-17T00:00:00',
 'RatingKey': 'fhrs_5_en-gb',
 'RatingValue': '5',
 'RightToReply': '',
 'SchemeType': 'FHRS',
 '_id': ObjectId('670c4b27a7644b19c7d9f980'),
 'geocode': {'latitude': '51.152225', 'longitude': '1.387974'},
 'links': [{'href': 'https://api.ratings.food.gov.uk/establishments/1034540',
            'rel': 'self'}],
 'meta': {'dataSource': None,
          'extractDate': '0001-01-01T0

In [11]:
# assign the collection to a variable
establishments = db['establishments']

## Part 2: Update the Database

1. An exciting new halal restaurant just opened in Greenwich, but hasn't been rated yet. The magazine has asked you to include it in your analysis. Add the following restaurant "Penang Flavours" to the database.

In [20]:
# Create a dictionary for the new restaurant data
new_restaurant = {
    "BusinessName":"Penang Flavours",
    "BusinessType":"Restaurant/Cafe/Canteen",
    "BusinessTypeID":"",
    "AddressLine1":"Penang Flavours",
    "AddressLine2":"146A Plumstead Rd",
    "AddressLine3":"London",
    "AddressLine4":"",
    "PostCode":"SE18 7DY",
    "Phone":"",
    "LocalAuthorityCode":"511",
    "LocalAuthorityName":"Greenwich",
    "LocalAuthorityWebSite":"http://www.royalgreenwich.gov.uk",
    "LocalAuthorityEmailAddress":"health@royalgreenwich.gov.uk",
    "scores":{
        "Hygiene":"",
        "Structural":"",
        "ConfidenceInManagement":""
    },
    "SchemeType":"FHRS",
    "geocode":{
        "longitude":"0.08384000",
        "latitude":"51.49014200"
    },
    "RightToReply":"",
    "Distance":4623.9723280747176,
    "NewRatingPending":True
}

In [21]:
# Insert the new restaurant into the collection
result = establishments.insert_one(new_restaurant)

In [23]:
# Check that the new restaurant was inserted
query = {'BusinessName': 'Penang Flavours'}
results = establishments.find(query)
for result in results:
    pprint(result)

{'AddressLine1': 'Penang Flavours',
 'AddressLine2': '146A Plumstead Rd',
 'AddressLine3': 'London',
 'AddressLine4': '',
 'BusinessName': 'Penang Flavours',
 'BusinessType': 'Restaurant/Cafe/Canteen',
 'BusinessTypeID': '',
 'Distance': 4623.972328074718,
 'LocalAuthorityCode': '511',
 'LocalAuthorityEmailAddress': 'health@royalgreenwich.gov.uk',
 'LocalAuthorityName': 'Greenwich',
 'LocalAuthorityWebSite': 'http://www.royalgreenwich.gov.uk',
 'NewRatingPending': True,
 'Phone': '',
 'PostCode': 'SE18 7DY',
 'RightToReply': '',
 'SchemeType': 'FHRS',
 '_id': ObjectId('670c77a0e8be7bab472eecde'),
 'geocode': {'latitude': '51.49014200', 'longitude': '0.08384000'},
 'scores': {'ConfidenceInManagement': '', 'Hygiene': '', 'Structural': ''}}


2. Find the BusinessTypeID for "Restaurant/Cafe/Canteen" and return only the `BusinessTypeID` and `BusinessType` fields.

In [32]:
# Find the BusinessTypeID for "Restaurant/Cafe/Canteen" and return only the BusinessTypeID and BusinessType fields
business_type = establishments.find_one(
    {"BusinessType": "Restaurant/Cafe/Canteen"},  # Query for matching BusinessType
    {"BusinessTypeID": 1, "BusinessType": 1, "_id": 0}  # Project only BusinessTypeID and BusinessType, exclude _id
)

for business_type in result:
    print(business_type)

3. Update the new restaurant with the `BusinessTypeID` you found.

In [33]:
# Update the new restaurant with the correct BusinessTypeID
if business_type:
    business_type_id = business_type["BusinessTypeID"]
    
update_result = establishments.update_one(
        {"BusinessName": "Penang Flavours"},  # Find the new restaurant
        {"$set": {"BusinessTypeID": business_type_id}}  # Set the correct BusinessTypeID
    )

In [34]:
# Confirm that the new restaurant was updated
if update_result.modified_count > 0:
        print("Restaurant 'Penang Flavours' successfully updated with BusinessTypeID.")
else:
        print("Restaurant 'Penang Flavours' was not updated.")

Restaurant 'Penang Flavours' successfully updated with BusinessTypeID.


4. The magazine is not interested in any establishments in Dover, so check how many documents contain the Dover Local Authority. Then, remove any establishments within the Dover Local Authority from the database, and check the number of documents to ensure they were deleted.

In [37]:
# Find how many documents have LocalAuthorityName as "Dover"
dover_count = establishments.count_documents({"LocalAuthorityName": "Dover"})
print(f"Number of establishments in Dover: {dover_count}")

Number of establishments in Dover: 994


In [38]:
# Delete all documents where LocalAuthorityName is "Dover"
delete_result = establishments.delete_many({"LocalAuthorityName": "Dover"})
print(f"Number of establishments deleted: {delete_result.deleted_count}")

Number of establishments deleted: 994


In [41]:
# Check if any remaining documents include Dover
remaining_dover_count = establishments.count_documents({"LocalAuthority": "Dover"})

if remaining_dover_count > 0:
    print(f"There are still {remaining_dover_count} establishments in Dover.")
else:
    print("No establishments in Dover remaining.")

No establishments in Dover remaining.


In [44]:
# Check that other documents remain with 'find_one'
remaining_document = establishments.find_one()

if remaining_document:
    pprint("There is at least one remaining establishment:")
    pprint(remaining_document)
else:
    print("No establishments remain in the database.")

'There is at least one remaining establishment:'
{'AddressLine1': 'East Cliff Pavilion',
 'AddressLine2': 'Wear Bay Road',
 'AddressLine3': 'Folkestone',
 'AddressLine4': 'Kent',
 'BusinessName': 'The Pavilion',
 'BusinessType': 'Restaurant/Cafe/Canteen',
 'BusinessTypeID': 1,
 'ChangesByServerID': 0,
 'Distance': 4591.765489457773,
 'FHRSID': 1043695,
 'LocalAuthorityBusinessID': 'PI/000073616',
 'LocalAuthorityCode': '188',
 'LocalAuthorityEmailAddress': 'foodteam@folkestone-hythe.gov.uk',
 'LocalAuthorityName': 'Folkestone and Hythe',
 'LocalAuthorityWebSite': 'http://www.folkestone-hythe.gov.uk',
 'NewRatingPending': False,
 'Phone': '',
 'PostCode': 'CT19 6BL',
 'RatingDate': '2018-04-04T00:00:00',
 'RatingKey': 'fhrs_5_en-gb',
 'RatingValue': '5',
 'RightToReply': '',
 'SchemeType': 'FHRS',
 '_id': ObjectId('670c4b27a7644b19c7d9fc65'),
 'geocode': {'latitude': '51.083812', 'longitude': '1.195625'},
 'links': [{'href': 'https://api.ratings.food.gov.uk/establishments/1043695',
    

5. Some of the number values are stored as strings, when they should be stored as numbers.

Use `update_many` to convert `latitude` and `longitude` to decimal numbers.

In [45]:
# Change the data type from String to Decimal for longitude and latitude
establishments.update_many({}, [ {'$set':{ "geocode.latitude" : {'$toDouble': "$geocode.latitude"},"geocode.longitude" : {'$toDouble': "$geocode.longitude"} }} ])

UpdateResult({'n': 38786, 'nModified': 38786, 'ok': 1.0, 'updatedExisting': True}, acknowledged=True)

Use `update_many` to convert `RatingValue` to integer numbers.

In [46]:
# Set non 1-5 Rating Values to Null
non_ratings = ["AwaitingInspection", "Awaiting Inspection", "AwaitingPublication", "Pass", "Exempt"]
establishments.update_many({"RatingValue": {"$in": non_ratings}}, [ {'$set':{ "RatingValue" : None}} ])

UpdateResult({'n': 4091, 'nModified': 4091, 'ok': 1.0, 'updatedExisting': True}, acknowledged=True)

In [47]:
# Change the data type from String to Integer for RatingValue
establishments.update_many({}, [ {'$set':{ "RatingValue" : {'$toInt': "$RatingValue"} }} ])

UpdateResult({'n': 38786, 'nModified': 34695, 'ok': 1.0, 'updatedExisting': True}, acknowledged=True)

In [48]:
# Check that the coordinates and rating value are now numbers
query = {}
fields = {'geocode.latitude': 1, 'geocode.longitude': 1, 'RatingValue': 1}

# Capture the results to a variable
results = establishments.find(query, fields)

# Pretty print the results
for result in results:
    pprint(result)

{'RatingValue': 5,
 '_id': ObjectId('670c4b27a7644b19c7d9fc65'),
 'geocode': {'latitude': 51.083812, 'longitude': 1.195625}}
{'RatingValue': 4,
 '_id': ObjectId('670c4b27a7644b19c7d9fc66'),
 'geocode': {'latitude': 51.086058, 'longitude': 1.196408}}
{'RatingValue': 5,
 '_id': ObjectId('670c4b27a7644b19c7d9fc67'),
 'geocode': {'latitude': 51.085797, 'longitude': 1.194762}}
{'RatingValue': 4,
 '_id': ObjectId('670c4b27a7644b19c7d9fc6c'),
 'geocode': {'latitude': 51.08084, 'longitude': 1.188537}}
{'RatingValue': 5,
 '_id': ObjectId('670c4b27a7644b19c7d9fc6d'),
 'geocode': {'latitude': 51.0783519967076, 'longitude': 1.18590330311705}}
{'RatingValue': 5,
 '_id': ObjectId('670c4b27a7644b19c7d9fc6e'),
 'geocode': {'latitude': 51.08084, 'longitude': 1.188537}}
{'RatingValue': 5,
 '_id': ObjectId('670c4b27a7644b19c7d9fc6f'),
 'geocode': {'latitude': 51.0783519967076, 'longitude': 1.18590330311705}}
{'RatingValue': 5,
 '_id': ObjectId('670c4b27a7644b19c7d9fc70'),
 'geocode': {'latitude': 51.0808